# Import

In [1]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import tensorflow as tf
import keras
import math
import datetime, os
from keras.callbacks import EarlyStopping
from sklearn import preprocessing
from sklearn.preprocessing import MinMaxScaler
import itertools
from kernels.gaussian_kernel_regression import gaussian_kernel_regression
from functions.common_function import *
from functions.initialize_model import initialize_model_expanded
from functions.cross_validation import cross_validation_split
from functions.dataset_interpolation import dataset_interpolation_own
from scipy.stats import pearsonr

'''Enabling plotting of graphs just below the plotting commands'''
%matplotlib inline
'''Enabling the disply of all rows and columns within the dataframe'''
pd.set_option("display.max_rows", None, "display.max_columns", None)

# Constant

In [2]:
num_feature = 8
cat_col = [4, 5]
num_ori_feature = num_feature - len(cat_col)
num_target = 3
bandwidth = 100
num_epochs = 10000
num_batch = 10
num_folds = 4
directory_name = "Counter_Choudhury_Method_Own_Gaussian_Kernel"

limit = pd.DataFrame({'lower' : [303, 20, 0, 2, 6, 1.5, 122, 1236, 14], \
                     'higher' : [840, 44, 17, 5, 8, 2, 408, 3240, 101], \
                     'ref' : [530, 40, 14, 3.2, 6, 1.8, np.nan, np.nan, np.nan]})

'''Import dataset'''
dataset = pd.read_csv("Dataset/Choudhury_Dataset.csv")

# Implementation

In [3]:
'''Iterate 10 times to mimic Cross Validation'''
MAE = []
MSE = []
RMSE = []

folds = cross_validation_split(dataset, num_folds)


'''Cross Validation'''
for i in range(len(folds)):
    test_index = [folds[i]]
    train_index = [fold for fold in folds if fold not in test_index]
    test_index = list(itertools.chain.from_iterable(test_index))
    train_index = list(itertools.chain.from_iterable(train_index))
    
    '''Dataset Interpolation'''
    interpolated_dataset = dataset_interpolation_own(dataset.iloc[train_index], num_ori_feature, num_target, limit, bandwidth)
    
    '''Converting Categorical Data into binary representation'''
    converted_dataset = convert_cat(interpolated_dataset, cat_col, num_ori_feature, num_target, [interpolated_dataset.iloc[:, 4].unique(), interpolated_dataset.iloc[:, 5].unique()])
    converted_test_dataset = convert_cat(dataset.iloc[test_index], cat_col, num_ori_feature, num_target, [dataset.iloc[:, 4].unique(), dataset.iloc[:, 5].unique()])

    '''Normalising dataset using Min Max present in the train set'''
    scaler = MinMaxScaler()
    scaler.fit(converted_dataset)
    
    '''Normalising of train and test set'''
    normalised_train_dataset = pd.DataFrame(scaler.transform(converted_dataset), columns = get_col_names(converted_dataset))
    normalised_test_dataset = pd.DataFrame(scaler.transform(converted_test_dataset), columns = get_col_names(converted_dataset))
    
    x_train = normalised_train_dataset.iloc[:, 0: num_feature]
    y_train =  normalised_train_dataset.iloc[:, num_feature: num_feature + num_target]
    x_test = normalised_test_dataset.iloc[:, 0: num_feature]
    y_test = normalised_test_dataset.iloc[:, num_feature: num_feature + num_target]

    model = initialize_model_expanded(num_feature, num_target, 'relu')
    
    '''Model Fitting'''
    print('------------------------------------------------------------------------')
    print(f'Training for iteration {i + 1} ...')
    
    '''Initializing early stopping that prevents overfitting
    and tensorboard for visualizing machine learning workflow'''
    early_stopping = EarlyStopping(monitor = 'loss', mode = 'min', verbose = 1, patience = 1800)
    logdir = os.path.join(f"logs/{directory_name}", "ANN_" + str(i + 1))
    tensorboard_callback = tf.keras.callbacks.TensorBoard(logdir, \
                                                         histogram_freq = 1,
                                                         write_graph = True,\
                                                         write_images = True)
    
    history = model.fit(x_train,\
                        y_train,
                        epochs = num_epochs,\
                        batch_size = num_batch,\
                        callbacks = [tensorboard_callback, early_stopping])
    
    '''Index 0 of result is represented by Mean Absolute Error'''
    result = model.evaluate(x_test, y_test, batch_size = 128)
    MAE.append(result[0])
    MSE.append(result[1])
    RMSE.append(result[2])
    model.save(f"Model\{directory_name}\model_{i + 1}")
    print("Saved model to disk")    
    print(f'Score for fold {i + 1}: {model.metrics_names[0]} of {result[0]}')

'''Provide average score'''
print('------------------------------------------------------------------------')
print('Score per fold')
for i in range(0, len(MAE)):
    print('------------------------------------------------------------------------')
    print(f'> Iteration {i+1} - MAE: {MAE[i]} - MSE: {MSE[i]}- RMSE: {RMSE[i]}') 
print('------------------------------------------------------------------------')
print('Average scores for all folds:')
print(f'> MAE: {np.mean(MAE)} - Standard Deviation: {np.std(MAE)}')
print(f'> MSE: {np.mean(MSE)}')
print(f'> RMSE: {np.mean(RMSE)}')
print('------------------------------------------------------------------------')

------------------------------------------------------------------------
Training for iteration 1 ...
Epoch 1/10000
 1/59 [..............................] - ETA: 0s - loss: 0.9132 - mean_squared_error: 0.8403 - root_mean_squared_error: 0.9167WARNING:tensorflow:From C:\Users\hfyyl2\.conda\envs\liew_new\lib\site-packages\tensorflow\python\ops\summary_ops_v2.py:1277: stop (from tensorflow.python.eager.profiler) is deprecated and will be removed after 2020-07-01.
Instructions for updating:
use `tf.profiler.experimental.stop` instead.
59/59 [==============================] - 0s 2ms/step - loss: 0.6684 - mean_squared_error: 0.5207 - root_mean_squared_error: 0.7216
Epoch 2/10000
59/59 [==============================] - 0s 900us/step - loss: 0.4575 - mean_squared_error: 0.3311 - root_mean_squared_error: 0.5755
Epoch 3/10000
59/59 [==============================] - 0s 899us/step - loss: 0.3888 - mean_squared_error: 0.3091 - root_mean_squared_error: 0.5560
Epoch 4/10000
59/59 [==================

59/59 [==============================] - 0s 924us/step - loss: 0.3364 - mean_squared_error: 0.2771 - root_mean_squared_error: 0.5264
Epoch 51/10000
59/59 [==============================] - 0s 882us/step - loss: 0.3356 - mean_squared_error: 0.2768 - root_mean_squared_error: 0.5261
Epoch 52/10000
59/59 [==============================] - 0s 967us/step - loss: 0.3350 - mean_squared_error: 0.2764 - root_mean_squared_error: 0.5257
Epoch 53/10000
59/59 [==============================] - 0s 899us/step - loss: 0.3345 - mean_squared_error: 0.2761 - root_mean_squared_error: 0.5254
Epoch 54/10000
59/59 [==============================] - 0s 908us/step - loss: 0.3338 - mean_squared_error: 0.2756 - root_mean_squared_error: 0.5250
Epoch 55/10000
59/59 [==============================] - 0s 899us/step - loss: 0.3330 - mean_squared_error: 0.2752 - root_mean_squared_error: 0.5246
Epoch 56/10000
59/59 [==============================] - 0s 967us/step - loss: 0.3325 - mean_squared_error: 0.2746 - root_mean_s

59/59 [==============================] - 0s 933us/step - loss: 0.3050 - mean_squared_error: 0.2632 - root_mean_squared_error: 0.5130
Epoch 106/10000
59/59 [==============================] - 0s 933us/step - loss: 0.3046 - mean_squared_error: 0.2630 - root_mean_squared_error: 0.5128
Epoch 107/10000
59/59 [==============================] - 0s 916us/step - loss: 0.3052 - mean_squared_error: 0.2630 - root_mean_squared_error: 0.5129
Epoch 108/10000
59/59 [==============================] - 0s 891us/step - loss: 0.3038 - mean_squared_error: 0.2629 - root_mean_squared_error: 0.5127
Epoch 109/10000
59/59 [==============================] - 0s 899us/step - loss: 0.3042 - mean_squared_error: 0.2628 - root_mean_squared_error: 0.5127
Epoch 110/10000
59/59 [==============================] - 0s 912us/step - loss: 0.3035 - mean_squared_error: 0.2626 - root_mean_squared_error: 0.5124
Epoch 111/10000
59/59 [==============================] - 0s 901us/step - loss: 0.3027 - mean_squared_error: 0.2625 - root_

59/59 [==============================] - 0s 891us/step - loss: 0.0441 - mean_squared_error: 0.0101 - root_mean_squared_error: 0.1007
Epoch 161/10000
59/59 [==============================] - 0s 899us/step - loss: 0.0428 - mean_squared_error: 0.0098 - root_mean_squared_error: 0.0988
Epoch 162/10000
59/59 [==============================] - 0s 892us/step - loss: 0.0434 - mean_squared_error: 0.0094 - root_mean_squared_error: 0.0967
Epoch 163/10000
59/59 [==============================] - 0s 900us/step - loss: 0.0417 - mean_squared_error: 0.0090 - root_mean_squared_error: 0.0948
Epoch 164/10000
59/59 [==============================] - 0s 907us/step - loss: 0.0410 - mean_squared_error: 0.0087 - root_mean_squared_error: 0.0931
Epoch 165/10000
59/59 [==============================] - 0s 916us/step - loss: 0.0417 - mean_squared_error: 0.0084 - root_mean_squared_error: 0.0919
Epoch 166/10000
59/59 [==============================] - 0s 916us/step - loss: 0.0399 - mean_squared_error: 0.0081 - root_

59/59 [==============================] - 0s 920us/step - loss: 0.0248 - mean_squared_error: 0.0017 - root_mean_squared_error: 0.0418
Epoch 215/10000
59/59 [==============================] - 0s 882us/step - loss: 0.0252 - mean_squared_error: 0.0018 - root_mean_squared_error: 0.0420
Epoch 216/10000
59/59 [==============================] - 0s 876us/step - loss: 0.0240 - mean_squared_error: 0.0016 - root_mean_squared_error: 0.0405
Epoch 217/10000
59/59 [==============================] - 0s 888us/step - loss: 0.0239 - mean_squared_error: 0.0016 - root_mean_squared_error: 0.0396
Epoch 218/10000
59/59 [==============================] - 0s 882us/step - loss: 0.0238 - mean_squared_error: 0.0016 - root_mean_squared_error: 0.0400
Epoch 219/10000
59/59 [==============================] - 0s 916us/step - loss: 0.0235 - mean_squared_error: 0.0015 - root_mean_squared_error: 0.0388
Epoch 220/10000
59/59 [==============================] - 0s 899us/step - loss: 0.0227 - mean_squared_error: 0.0015 - root_

...

59/59 [==============================] - 0s 648us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2811/10000
59/59 [==============================] - 0s 698us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2812/10000
59/59 [==============================] - 0s 764us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2813/10000
59/59 [==============================] - 0s 879us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2814/10000
59/59 [==============================] - 0s 639us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2815/10000
59/59 [==============================] - 0s 787us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2816/10000
59/59 [==============================] - 0s 1ms/step - loss: 0.1952 - mean_squared_error: 0.1255 - r

59/59 [==============================] - 0s 764us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2865/10000
59/59 [==============================] - 0s 1ms/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2866/10000
59/59 [==============================] - 0s 942us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2867/10000
59/59 [==============================] - 0s 944us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2868/10000
59/59 [==============================] - 0s 777us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2869/10000
59/59 [==============================] - 0s 899us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2870/10000
59/59 [==============================] - 0s 809us/step - loss: 0.1952 - mean_squared_error: 0.1255 - r

59/59 [==============================] - 0s 699us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2919/10000
59/59 [==============================] - 0s 936us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2920/10000
59/59 [==============================] - 0s 886us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2921/10000
59/59 [==============================] - 0s 760us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2922/10000
59/59 [==============================] - 0s 702us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2923/10000
59/59 [==============================] - 0s 954us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2924/10000
59/59 [==============================] - 0s 1ms/step - loss: 0.1952 - mean_squared_error: 0.1255 - r

59/59 [==============================] - 0s 897us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2973/10000
59/59 [==============================] - 0s 942us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2974/10000
59/59 [==============================] - 0s 873us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2975/10000
59/59 [==============================] - 0s 667us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2976/10000
59/59 [==============================] - 0s 851us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2977/10000
59/59 [==============================] - 0s 905us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 2978/10000
59/59 [==============================] - 0s 837us/step - loss: 0.1952 - mean_squared_error: 0.1255 -

59/59 [==============================] - 0s 830us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 3027/10000
59/59 [==============================] - 0s 973us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 3028/10000
59/59 [==============================] - 0s 785us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 3029/10000
59/59 [==============================] - 0s 703us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 3030/10000
59/59 [==============================] - 0s 896us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 3031/10000
59/59 [==============================] - 0s 946us/step - loss: 0.1952 - mean_squared_error: 0.1255 - root_mean_squared_error: 0.3542
Epoch 3032/10000
59/59 [==============================] - 0s 821us/step - loss: 0.1952 - mean_squared_error: 0.1255 -

###  Loading of Model

In [4]:
'''Loads the Best Model Trained using Cross Validation'''
loaded_model = keras.models.load_model(f"Model\{directory_name}\model_{MAE.index(min(MAE)) + 1}")
print("Loaded model from disk")

'''Compilation of the model with its corresponding weights, followed by the evaluation of the model using test set'''
loaded_model.compile(loss = 'MeanAbsoluteError',\
                    optimizer = 'SGD',\
                    metrics = [tf.keras.metrics.MeanSquaredError(),\
                    tf.keras.metrics.RootMeanSquaredError()])

Loaded model from disk


# Visualisation of Predictions using Best Model from Cross Validation

In [5]:
'''Converting Categorical Data into binary representation'''
converted_visualise_dataset = convert_cat(dataset, cat_col, num_ori_feature, num_target, [dataset.iloc[:, 4].unique(), dataset.iloc[:, 5].unique()])

'''Feature Target Splitting'''
scaler = MinMaxScaler()
scaler.fit(converted_visualise_dataset)
normalised_dataset = pd.DataFrame(scaler.transform(converted_visualise_dataset), columns = get_col_names(converted_visualise_dataset))
feature, target = x_y_split(normalised_dataset, num_feature, num_target)
prediction = pd.DataFrame(loaded_model.predict(feature), columns = get_col_names(target))

'''Preparation to Rescale target values'''
min_y = dataset.iloc[:, num_ori_feature: num_ori_feature + num_target].min().to_list()
max_y = dataset.iloc[:, num_ori_feature: num_ori_feature + num_target].max().to_list()

corr_list = []
'''Tabulating the differences of Expected and Predictions made by the ANN Model'''
for i in range(len(feature)):
    '''Rescaling of normalised data'''
    expected = pd.DataFrame(inverse_transform(target.iloc[i].to_list(), max_y, min_y))
    predicted = pd.DataFrame(inverse_transform(prediction.iloc[i].to_list(), max_y, min_y))
    comparison_df = pd.concat([expected, predicted], axis = 1)
    comparison_df.columns = ['Expected', 'Predicted']
    comparison_df.index = get_col_names(target)
    display(comparison_df.style.set_caption(f"Element {i + 1}"))
    corr, _ = pearsonr(expected.iloc[:, 0].tolist(), predicted.iloc[:, 0].tolist())
    corr_list.append(corr)

'''Provide average score'''
print('------------------------------------------------------------------------')
print('Score per fold')
for i in range(0, len(corr_list)):
    print('------------------------------------------------------------------------')
    print(f'> Iteration {i+1} - Pearson Correlation: {corr_list[i]}') 
print('------------------------------------------------------------------------')
print('Average scores for all folds:')
print(f'> Average Pearsons Correlation: {np.mean(corr_list)} - Standard Deviation: {np.std(corr_list)}')
print('------------------------------------------------------------------------')  

------------------------------------------------------------------------
Score per fold
------------------------------------------------------------------------
> Iteration 1 - Pearson Correlation: 0.9999990803325574
------------------------------------------------------------------------
> Iteration 2 - Pearson Correlation: 0.9997179308236646
------------------------------------------------------------------------
> Iteration 3 - Pearson Correlation: 0.9999903813747184
------------------------------------------------------------------------
> Iteration 4 - Pearson Correlation: 0.9994131982620913
------------------------------------------------------------------------
> Iteration 5 - Pearson Correlation: 0.9997076695299307
------------------------------------------------------------------------
> Iteration 6 - Pearson Correlation: 0.9997385812874933
------------------------------------------------------------------------
> Iteration 7 - Pearson Correlation: 0.9997308034485481
---------